# Load Markets for One Specific Event


In [48]:
import requests, json

event_ticker = "KXPRESPERSON-28"
url = f"https://api.elections.kalshi.com/trade-api/v2/events/{event_ticker}?with_nested_markets=true"
response = requests.get(url)
oneEventMarkets = response.json()
print(json.dumps(oneEventMarkets, indent=4))

{
    "event": {
        "available_on_brokers": true,
        "category": "Elections",
        "collateral_return_type": "MECNET",
        "event_ticker": "KXPRESPERSON-28",
        "markets": [
            {
                "can_close_early": true,
                "close_time": "2029-11-07T15:00:00Z",
                "created_time": "0001-01-01T00:00:00Z",
                "custom_strike": {
                    "Pres candidate": "Gavin Newsom"
                },
                "early_close_condition": "This market will close and expire after a person has been inaugurated as President pursuant to the next presidential election.",
                "event_ticker": "KXPRESPERSON-28",
                "expected_expiration_time": "2029-01-21T15:00:00Z",
                "expiration_time": "2029-11-07T15:00:00Z",
                "expiration_value": "",
                "last_price": 20,
                "last_price_dollars": "0.2000",
                "latest_expiration_time": "2029-11-07T15:00:0

In [49]:
# Converting Events and Markets to DataFrames:
import pandas as pd
pd.set_option('display.max_columns', None)
events_df = pd.json_normalize(oneEventMarkets["event"])
events_df.head()

available_on_brokers   category collateral_return_type     event_ticker  \
0                  True  Elections                 MECNET  KXPRESPERSON-28   

                                             markets  mutually_exclusive  \
0  [{'can_close_early': True, 'close_time': '2029...                True   

  series_ticker strike_period sub_title  \
0  KXPRESPERSON                 In 2028   

                                     title  
0  Next U.S. Presidential Election Winner?

In [50]:
import psycopg2

# connection establishment
conn = psycopg2.connect(
   database="postgres",
    user='postgres',
    password='kek',
    host='localhost',
    port= '5432'
)

conn.autocommit = True

# Creating a cursor object
cursor = conn.cursor()

# query to create a database 
sql = """
    Create table if not exists events (
        event_ticker TEXT PRIMARY KEY,
        series_ticker TEXT,
        title TEXT,
        sub_title TEXT,
        category TEXT,
        available_on_brokers BOOLEAN,
        mutually_exclusive BOOLEAN,
        collateral_return_type TEXT,
        strike_period TEXT,
        updated_at TIMESTAMPTZ DEFAULT now()
    );

    
    CREATE TABLE IF NOT EXISTS markets (
        market_ticker TEXT PRIMARY KEY,
        event_ticker TEXT,

        title       TEXT,
        subtitle    TEXT,
        market_type TEXT,                                
        status      TEXT, 

        can_close_early BOOLEAN,
        tick_size       SMALLINT,
        settlement_timer_seconds INTEGER, 

        open_time                TIMESTAMPTZ,
        close_time               TIMESTAMPTZ,
        expiration_time          TIMESTAMPTZ,
        expected_expiration_time TIMESTAMPTZ,
        latest_expiration_time   TIMESTAMPTZ,
        created_time             TIMESTAMPTZ,

        
        last_price     SMALLINT,
        previous_price SMALLINT,
        yes_ask        SMALLINT,
        yes_bid        SMALLINT,
        no_ask         SMALLINT,
        no_bid         SMALLINT,
        previous_yes_ask SMALLINT,
        previous_yes_bid SMALLINT,

        last_price_dollars       NUMERIC(10,4),
        previous_price_dollars   NUMERIC(10,4),
        yes_ask_dollars          NUMERIC(10,4),
        yes_bid_dollars          NUMERIC(10,4),
        no_ask_dollars           NUMERIC(10,4),
        no_bid_dollars           NUMERIC(10,4),
        previous_yes_ask_dollars NUMERIC(10,4),
        previous_yes_bid_dollars NUMERIC(10,4),

        
        liquidity        BIGINT,                         
        open_interest    BIGINT,
        volume           BIGINT,
        volume_24h       BIGINT,

        liquidity_dollars    NUMERIC(20,4),
        open_interest_fp     NUMERIC(20,2),
        volume_fp            NUMERIC(20,2),
        volume_24h_fp         NUMERIC(20,2),

        price_level_structure TEXT,                      
        response_price_units  TEXT,                       
        expiration_value      TEXT,
        result                TEXT,

        no_sub_title  TEXT,
        yes_sub_title TEXT,

        early_close_condition TEXT,
        rules_primary         TEXT,
        rules_secondary       TEXT,

        price_ranges JSONB,                              
        custom_strike JSONB,                             

        updated_at TIMESTAMPTZ DEFAULT now(), 

        CONSTRAINT fk_markets_event
            FOREIGN KEY(event_ticker)
            REFERENCES events(event_ticker)
            ON DELETE CASCADE
    );

    CREATE INDEX IF NOT EXISTS idx_markets_event_ticker ON markets(event_ticker);
    CREATE INDEX IF NOT EXISTS idx_markets_status ON markets(status);


    CREATE TABLE IF NOT EXISTS candles (
        market_ticker TEXT NOT NULL,
        interval_min  INTEGER NOT NULL,           -- period_interval you requested (1, 60, 1440, etc.)
        end_ts        TIMESTAMPTZ NOT NULL,        -- derived from end_period_ts (unix seconds)

        -- trades (may be NULL if no trades in bucket)
        trade_open    SMALLINT,
        trade_high    SMALLINT,
        trade_low     SMALLINT,
        trade_close   SMALLINT,
        trade_prev    SMALLINT,                   -- price.previous

        -- bid/ask quote candles (usually present)
        yes_bid_open  SMALLINT,
        yes_bid_high  SMALLINT,
        yes_bid_low   SMALLINT,
        yes_bid_close SMALLINT,

        yes_ask_open  SMALLINT,
        yes_ask_high  SMALLINT,
        yes_ask_low   SMALLINT,
        yes_ask_close SMALLINT,

        -- activity
        volume        BIGINT NOT NULL DEFAULT 0,
        open_interest BIGINT,

        created_at    TIMESTAMPTZ NOT NULL DEFAULT now(),


        CONSTRAINT pk_candles PRIMARY KEY (market_ticker, interval_min, end_ts),
        CONSTRAINT fk_candles_market FOREIGN KEY (market_ticker)
            REFERENCES markets(market_ticker)
            ON DELETE CASCADE
    );

    CREATE INDEX IF NOT EXISTS idx_candles_market_interval_endts
    ON candles (market_ticker, interval_min, end_ts DESC);

    """;

# executing above query
cursor.execute(sql)
print("Database has been created successfully !!!");



Database has been created successfully !!!


In [51]:
# Print
with conn, conn.cursor() as cur:
    cur.execute("SELECT * FROM events;")
    rows = cur.fetchall()
    for row in rows:
        print(row)

# Closing the connection
conn.close()

In [52]:
pd.set_option('display.max_columns', None)
markets_df = pd.json_normalize(oneEventMarkets["event"]["markets"], sep=".")
markets_df["event_ticker"] = oneEventMarkets["event"]["event_ticker"]
markets_df.head(30)

can_close_early            close_time          created_time  \
0              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
1              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
2              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
3              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
4              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
5              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
6              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
7              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
8              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
9              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
10             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
11             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
12             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
13             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
14             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
15             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
16             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
17             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
18             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
19             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
20             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
21             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
22             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   

                                early_close_condition     event_ticker  \
0   This market will close and expire after a pers...  KXPRESPERSON-28   
1   This market will close and expire after a pers...  KXPRESPERSON-28   
2   This market will close and expire after a pers...  KXPRESPERSON-28   
3   This market will close and expire after a pers...  KXPRESPERSON-28   
4   This market will close and expire after a pers...  KXPRESPERSON-28   
5   This market will close and expire after a pers...  KXPRESPERSON-28   
6   This market will close and expire after a pers...  KXPRESPERSON-28   
7   This market will close and expire after a pers...  KXPRESPERSON-28   
8   This market will close and expire after a pers...  KXPRESPERSON-28   
9   This market will close and expire after a pers...  KXPRESPERSON-28   
10  This market will close and expire after a pers...  KXPRESPERSON-28   
11  This market will close and expire after a pers...  KXPRESPERSON-28   
12  This market will close and expire after a pers...  KXPRESPERSON-28   
13  This market will close and expire after a pers...  KXPRESPERSON-28   
14  This market will close and expire after a pers...  KXPRESPERSON-28   
15  This market will close and expire after a pers...  KXPRESPERSON-28   
16  This market will close and expire after a pers...  KXPRESPERSON-28   
17  This market will close and expire after a pers...  KXPRESPERSON-28   
18  This market will close and expire after a pers...  KXPRESPERSON-28   
19  This market will close and expire after a pers...  KXPRESPERSON-28   
20  This market will close and expire after a pers...  KXPRESPERSON-28   
21  This market will close and expire after a pers...  KXPRESPERSON-28   
22  This market will close and expire after a pers...  KXPRESPERSON-28   

   expected_expiration_time       expiration_time expiration_value  \
0      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
1      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
2      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
3      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
4      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
5      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
6      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
7      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z         

In [67]:
import requests
from datetime import datetime, timezone

marketsCandles = {}


for market in oneEventMarkets["event"]["markets"]:
    market_ticker = market["ticker"]
    now_utc = datetime.now(timezone.utc)
    created_time = int(datetime.fromisoformat(market["created_time"].replace("Z", "+00:00")).timestamp())
    end_ts = int(now_utc.timestamp())
    start_ts = (end_ts - 24*60*60) if created_time <= (end_ts - 24*60*60) else created_time
    interval = 1

    params = {
        "market_tickers": market_ticker,   
        "start_ts": start_ts,
        "end_ts": end_ts,
        "period_interval": 1,              
        "include_latest_before_start": "true",
    }
    
    url = f"https://api.elections.kalshi.com/trade-api/v2/markets/candlesticks"
    try:
        response = requests.get(url, params=params, timeout=10)
        oneMarketCandles = response.json()
        marketsCandles[market_ticker] = oneMarketCandles
    except Exception as e:
        print(f"Error fetching markets for event {event_ticker}: {e}")
print(json.dumps(marketsCandles, indent=4))

{
    "KXPRESPERSON-28-GNEWS": {
        "markets": [
            {
                "candlesticks": [
                    {
                        "end_period_ts": 1769807460,
                        "open_interest": 659262,
                        "open_interest_fp": "659262.00",
                        "price": {
                            "close": null,
                            "high": null,
                            "low": null,
                            "max": null,
                            "mean": null,
                            "min": null,
                            "open": null,
                            "previous": 20,
                            "previous_dollars": "0.2000"
                        },
                        "volume": 0,
                        "volume_fp": "0.00",
                        "yes_ask": {
                            "close": 20,
                            "close_dollars": "0.2000",
                            "high": 20,
       

In [68]:
marketsCandles_df_list = []
for market_ticker in marketsCandles:
    candlesticks = marketsCandles[market_ticker]["markets"][0]["candlesticks"]

    candles_df = pd.DataFrame([
        {
            'market_ticker': market_ticker,
            'timestamp': datetime.fromtimestamp(c['end_period_ts']),
            # Use TRADE prices (what Kalshi chart shows)
            'trade_open': c.get('price', {}).get('open'),
            'trade_high': c.get('price', {}).get('high'),
            'trade_low': c.get('price', {}).get('low'),
            'trade_close': c.get('price', {}).get('close'),
            # Keep bid/ask for reference
            'yes_bid_close': c['yes_bid']['close'],
            'yes_ask_close': c['yes_ask']['close'],
            'mid_price': (c['yes_bid']['close'] + c['yes_ask']['close']) / 2,
            'volume': c['volume'],
            'open_interest': c['open_interest'],
        }
        for c in candlesticks
    ])
    if len(marketsCandles_df_list) == 0:
        marketsCandles_df_list = candles_df
    else:
        marketsCandles_df_list = pd.concat([marketsCandles_df_list, candles_df], ignore_index=True)
        

marketsCandles_df_list.head(30)




/var/folders/83/t702v3093vj_m1cq21gyvzgh0000gn/T/ipykernel_79445/2060446739.py:26: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



market_ticker           timestamp  trade_open  trade_high  \
0   KXPRESPERSON-28-GNEWS 2026-01-31 03:11:00         NaN         NaN   
1   KXPRESPERSON-28-GNEWS 2026-01-31 03:15:00         NaN         NaN   
2   KXPRESPERSON-28-GNEWS 2026-01-31 03:20:00        20.0        20.0   
3   KXPRESPERSON-28-GNEWS 2026-01-31 03:21:00         NaN         NaN   
4   KXPRESPERSON-28-GNEWS 2026-01-31 03:26:00         NaN         NaN   
5   KXPRESPERSON-28-GNEWS 2026-01-31 03:31:00         NaN         NaN   
6   KXPRESPERSON-28-GNEWS 2026-01-31 03:35:00         NaN         NaN   
7   KXPRESPERSON-28-GNEWS 2026-01-31 03:36:00         NaN         NaN   
8   KXPRESPERSON-28-GNEWS 2026-01-31 03:38:00        20.0        20.0   
9   KXPRESPERSON-28-GNEWS 2026-01-31 03:41:00         NaN         NaN   
10  KXPRESPERSON-28-GNEWS 2026-01-31 03:42:00         NaN         NaN   
11  KXPRESPERSON-28-GNEWS 2026-01-31 03:46:00        19.0        19.0   
12  KXPRESPERSON-28-GNEWS 2026-01-31 03:47:00         NaN         NaN   
13  KXPRESPERSON-28-GNEWS 2026-01-31 03:52:00         NaN         NaN   
14  KXPRESPERSON-28-GNEWS 2026-01-31 03:57:00         NaN         NaN   
15  KXPRESPERSON-28-GNEWS 2026-01-31 03:58:00        19.0        19.0   
16  KXPRESPERSON-28-GNEWS 2026-01-31 04:02:00         NaN         NaN   
17  KXPRESPERSON-28-GNEWS 2026-01-31 04:03:00        20.0        20.0   
18  KXPRESPERSON-28-GNEWS 2026-01-31 04:04:00        20.0        20.0   
19  KXPRESPERSON-28-GNEWS 2026-01-31 04:07:00         NaN         NaN   
20  KXPRESPERSON-28-GNEWS 2026-01-31 04:12:00        19.0        19.0   
21  KXPRESPERSON-28-GNEWS 2026-01-31 04:13:00         NaN         NaN   
22  KXPRESPERSON-28-GNEWS 2026-01-31 04:18:00         NaN         NaN   
23  KXPRESPERSON-28-GNEWS 2026-01-31 04:19:00         NaN         NaN   
24  KXPRESPERSON-28-GNEWS 2026-01-31 04:22:00         NaN         NaN   
25  KXPRESPERSON-28-GNEWS 2026-01-31 04:23:00        20.0        20.0   
26  KXPRESPERSON-28-GNEWS 2026-01-31 04:28:00         NaN         NaN   
27  KXPRESPERSON-28-GNEWS 2026-01-31 04:31:00         NaN         NaN   
28  KXPRESPERSON-28-GNEWS 2026-01-31 04:33:00         NaN         NaN   
29  KXPRESPERSON-28-GNEWS 2026-01-31 04:37:00         NaN         NaN   

    trade_low  trade_close  yes_bid_close  yes_ask_close  mid_price  volume  \
0         NaN          NaN             19             20       19.5       0   
1         NaN          NaN             19             20       19.5       0   
2        20.0         20.0             19             20       19.5       4   
3         NaN          NaN             19             20       19.5       0   
4         NaN          NaN             19             20       19.5       0   
5         NaN          NaN             19             20       19.5       0   
6         NaN          NaN             19             20       19.5       0   
7         NaN          NaN             19             20       19.5       0   
8        20.0         20.0             19             20       19.5     181   
9         NaN          NaN             19             20       19.5       0   
10        NaN          NaN             19             20       19.5       0   
11       19.0         19.0             19             20       19.5      14   
12        NaN          NaN             19             20       19.5       0   
13        NaN          NaN             19             20       19.5       0   
14        NaN          NaN             19             20       19.5       0   
15       19.0         19.0             19             20       19.5       5   
16        NaN          NaN             19             20       19.5       0   
17       20.0         20.0             19             20       19.5     236   
18       20.0         20.0             19             20       19.5      23   
19        NaN          NaN             19             20       19.5       0   
20       19.0         19.0             19             20       19.5      23   
21        

In [78]:
import pandas as pd
import plotly.graph_objects as go

fig = go.Figure()

market_avg = marketsCandles_df_list.groupby('market_ticker')['yes_bid_close'].mean().sort_values(ascending=False)
top_markets = market_avg[market_avg > 5].head(3).index.tolist()
df_filtered = marketsCandles_df_list[marketsCandles_df_list['market_ticker'].isin(top_markets)]
colors = ['blue', 'green', 'orange', 'red', 'purple']


for i, market in enumerate(top_markets):
    market_data = marketsCandles_df_list[marketsCandles_df_list['market_ticker'] == market]

    parts = market.split('-')
    name = parts[-1]

    # Use trade_close, forward-fill NaN values
    price_series = market_data['trade_close'].ffill()
    
    fig.add_trace(go.Scatter(
        x=market_data['timestamp'],
        y=price_series,
        name=name,
        mode='lines',
        line=dict(
            color=colors[i % len(colors)],
            width=2.5,
            shape='hv'
        ),
        hovertemplate=f'<b>{name}</b><br>%{{y}}%<extra></extra>'
    ))

fig.update_layout(
    title="Next U.S. Presidential Election Winner?",
    yaxis=dict(
        title='Probability (%)',
        range=[0, 40],
        
        tickformat='.1f',
        showgrid=True,
        gridcolor='#E5E7EB'
    ),
    plot_bgcolor='white',
    paper_bgcolor='white',
    height=550,
    width=1200,
    hovermode='x unified',
    legend=dict(
        orientation='v',
        yanchor='top',
        y=1,
        xanchor='right',
        x=1.15
    )
)

fig.show()

In [73]:
# First, let's see what your data actually looks like
df = marketsCandles_df_list

# Check one market in detail
test_market = df[df['market_ticker'] == 'KXPRESPERSON-28-JVAN'].copy()
print(f"Total candles: {len(test_market)}")
print(f"Unique yes_bid_close values: {test_market['trade_close'].nunique()}")
print(f"Price range: {test_market['trade_close'].min()} to {test_market['trade_close'].max()}")
print("\nFirst 10 rows:")
print(test_market[['timestamp', 'trade_close', 'volume']].head(10))

Total candles: 323
Unique yes_bid_close values: 3
Price range: 26.0 to 28.0

First 10 rows:
               timestamp  trade_close  volume
2334 2026-01-31 03:11:00          NaN       1
2335 2026-01-31 03:17:00         28.0       6
2336 2026-01-31 03:32:00         28.0       3
2337 2026-01-31 03:35:00          NaN       0
2338 2026-01-31 03:51:00         26.0      66
2339 2026-01-31 03:52:00         28.0      17
2340 2026-01-31 03:55:00          NaN       0
2341 2026-01-31 03:59:00          NaN       0
2342 2026-01-31 04:31:00         28.0      68
2343 2026-01-31 04:52:00          NaN       0


In [62]:
# Check ALL markets for price variation
df = marketsCandles_df_list

market_stats = df.groupby('market_ticker').agg({
    'yes_bid_close': ['min', 'max', 'nunique'],
    'volume': 'sum'
}).reset_index()

market_stats.columns = ['market_ticker', 'min_bid', 'max_bid', 'unique_prices', 'total_volume']
market_stats['price_range'] = market_stats['max_bid'] - market_stats['min_bid']

# Sort by most active (highest price variation)
market_stats = market_stats.sort_values('price_range', ascending=False)

print("Markets with most price variation:")
print(market_stats[market_stats['price_range'] > 0])

Markets with most price variation:
           market_ticker  min_bid  max_bid  unique_prices  total_volume  \
2   KXPRESPERSON-28-DTRU        2        3              2          3602   
14  KXPRESPERSON-28-MRUB       10       11              2          2740   

    price_range  
2             1  
14            1  


In [79]:
market_ticker = 'KXPRESPERSON-28-MRUB'
target_date = '2026-01-31'

filtered = df[
    (df['market_ticker'] == market_ticker) & 
    (df['timestamp'].dt.date == pd.to_datetime(target_date).date()) &
    (df['timestamp'].dt.hour == 21)  # 21 is 9 PM in 24-hour format
]

print(filtered.head())

             market_ticker           timestamp  trade_open  trade_high  \
3228  KXPRESPERSON-28-MRUB 2026-01-31 21:00:00         NaN         NaN   
3229  KXPRESPERSON-28-MRUB 2026-01-31 21:04:00         NaN         NaN   
3230  KXPRESPERSON-28-MRUB 2026-01-31 21:05:00         NaN         NaN   
3231  KXPRESPERSON-28-MRUB 2026-01-31 21:07:00         NaN         NaN   
3232  KXPRESPERSON-28-MRUB 2026-01-31 21:18:00         NaN         NaN   

      trade_low  trade_close  yes_bid_close  yes_ask_close  mid_price  volume  \
3228        NaN          NaN             10             11       10.5       0   
3229        NaN          NaN             10             11       10.5       0   
3230        NaN          NaN             10             11       10.5       0   
3231        NaN          NaN             10             11       10.5       0   
3232        NaN          NaN             10             11       10.5       0   

      open_interest  
3228         636424  
3229         636424  
32

In [81]:
# Check for the last known trade price around that time
market_ticker = 'KXPRESPERSON-28-MRUB'
target_date = '2026-01-31'

market_data = df[df['market_ticker'] == market_ticker].copy()

# Find rows where trade_close is not NaN (actual trades happened)
trades_only = market_data[market_data['trade_close'].notna()]
print(f"Total candles with actual trades: {len(trades_only)}")
print("\nRecent trades around 9 PM:")
trades_only[trades_only['timestamp'].dt.date == pd.to_datetime(target_date).date()][
    ['timestamp', 'trade_close', 'yes_bid_close', 'yes_ask_close', 'mid_price', 'volume']
].tail(20)

Total candles with actual trades: 23

Recent trades around 9 PM:


timestamp  trade_close  yes_bid_close  yes_ask_close  \
2962 2026-01-31 03:26:00         12.0             10             12   
2988 2026-01-31 06:25:00         12.0             10             12   
2991 2026-01-31 06:56:00         11.0             10             11   
2992 2026-01-31 07:01:00         12.0             10             11   
2997 2026-01-31 07:09:00         11.0             10             11   
3001 2026-01-31 07:24:00         11.0             10             11   
3027 2026-01-31 08:45:00         12.0             10             11   
3050 2026-01-31 09:55:00         11.0             10             11   
3060 2026-01-31 10:50:00         11.0             10             11   
3079 2026-01-31 12:03:00         10.0             10             11   
3089 2026-01-31 12:26:00         11.0             11             12   
3106 2026-01-31 13:18:00         10.0             10             11   
3204 2026-01-31 18:58:00         12.0             10             12   
3209 2026-01-31 19:10:00         10.0             10             11   
3217 2026-01-31 20:20:00         12.0             10             11   
3253 2026-01-31 22:22:00         11.0             10             11   
3276 2026-01-31 23:38:00         11.0             10             11   
3280 2026-01-31 23:43:00         11.0             10             11   

      mid_price  volume  
2962       11.0     163  
2988       11.0    1010  
2991       10.5       8  
2992       10.5     145  
2997       10.5      85  
3001       10.5      85  
3027       10.5     202  
3050       10.5     128  
3060       10.5     100  
3079       10.5      11  
3089       11.5      26  
3106       10.5       3  
3204       11.0     118  
3209       10.5       8  
3217       10.5      23  
3253       10.5      85  
3276       10.5      42  
3280       10.5       4

# Updating and Looping Requesting Candlestick Data


In [ ]:
import requests
import time
from datetime import datetime, timezone
from typing import Dict, List
import json


